In [543]:
import os
import numpy as np
import pandas as pd
import librosa as lr
import librosa.display
import glob
import matplotlib.pyplot as plt
import moviepy.editor as mp
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import OneHotEncoder
from sklearn.metrics import confusion_matrix, classification_report
from sklearn.ensemble import RandomForestClassifier
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Conv1D, MaxPooling1D, LSTM
from keras.utils import to_categorical
from keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow.keras.layers import BatchNormalization

In [450]:
EMOTIONS = {1:'neutral', 2:'calm', 3:'happy', 4:'sad', 5:'angry', 6:'fear', 7:'disgust', 0:'surprise'}

In [451]:
data = pd.DataFrame(columns=['Emotion', 'Emotion intensity', 'Gender','Path'])

In [452]:
dataset = []
files = glob.glob(fr'C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\projet_dl\projet_DL\dataset\*')
for folders in files:
    folder1 = glob.glob(fr'{folders}\*')
    
    dataset.extend(folder1)
    
    print(dataset)

['C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-01-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-01-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-02-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-01-01-02-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-01-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-01-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-02-01-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\ECE\\ING5\\DL\\projet_dl\\projet_DL\\dataset\\Actor_01\\03-01-02-01-02-02-01.wav', 'C:\\Users\\doria\\OneDrive\\Bureau\\EC

In [453]:
print(len(dataset))

2452


In [499]:
# Définir une fonction pour extraire les caractéristiques audio
def extract_features(file_path):
    # Charger le fichier audio avec Librosa
    y, sr = lr.load(file_path, sr=None)
    
    # Calculer le spectre mél
    mel_spec = librosa.feature.melspectrogram(y=y, sr=sr)
    
    # Calculer les coefficients cepstraux en fréquence (MFCC)
    mfcc = librosa.feature.mfcc(y=y, sr=sr, n_mfcc=13)
    mfcc = np.mean(mfcc.T, axis=0)
    
    # Calculer le chromagramme
    chroma = librosa.feature.chroma_stft(y=y, sr=sr)
    
    # Calculer le rythme
    tempo, _ = librosa.beat.beat_track(y=y, sr=sr)

    return  mel_spec, mfcc, chroma, tempo

In [475]:
# Définir les émotions
EMOTIONS = {1: 'neutral', 2: 'calm', 3: 'happy', 4: 'sad', 5: 'angry', 6: 'fear', 7: 'disgust', 8: 'surprise'}

# Chemin du dossier contenant les fichiers audio
DATA_PATH = fr'C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\projet_dl\projet_DL\dataset'

# Définir la liste pour stocker les données
data = []

# Parcourir les dossiers
folders = glob.glob(os.path.join(DATA_PATH, '*'))
for folder in folders:
    # Parcourir les fichiers dans chaque dossier
    folder1 = glob.glob(os.path.join(folder, '*'))
    for files1 in folder1:
        data1 = glob.glob(os.path.join(files1, '*'))
        
        y, sr = lr.load(files1, sr=None)
            
        # Extraire les informations du fichier
        identifiers = os.path.basename(files1).split('.')[0].split('-')
            
        modality = int(identifiers[0])
        vocal_channel = int(identifiers[1])
        emotion = int(identifiers[2])
        emotion_intensity = int(identifiers[3])
        statement = int(identifiers[4])
        repetition = int(identifiers[5])
        actor = int(identifiers[6])
            
        # Mapping des informations pour correspondre à notre structure
        emotion_mapping = {1: 'neutral', 2: 'calm', 3: 'happy', 4: 'sad', 5: 'angry', 6: 'fear', 7: 'disgust', 8: 'surprise'}
        #emotion = emotion_mapping[emotion]
        emotion_intensity = 'normal' if emotion_intensity == 1 else 'strong'            
        gender = 'female' if actor % 2 == 0 else 'male'
            
        # Ajouter les informations au DataFrame
        data.append({
            'Modality': modality,
            'Vocal Channel': vocal_channel,
            'Emotion': emotion,
            'Emotion_string': emotion_mapping[emotion],
            'Emotion Intensity': emotion_intensity,
            'Statement': statement,
            'Repetition': repetition,
            'Actor': actor,
            'Gender': gender,
            'Path': files1
         })

# Convertir la liste en DataFrame
df = pd.DataFrame(data)

# Afficher le DataFrame
print(df)

      Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0            3              1        1        neutral            normal   
1            3              1        1        neutral            normal   
2            3              1        1        neutral            normal   
3            3              1        1        neutral            normal   
4            3              1        2           calm            normal   
...        ...            ...      ...            ...               ...   
2447         3              2        6           fear            normal   
2448         3              2        6           fear            strong   
2449         3              2        6           fear            strong   
2450         3              2        6           fear            strong   
2451         3              2        6           fear            strong   

      Statement  Repetition  Actor  Gender  \
0             1           1      1    male   
1      

In [519]:
df_copy = df.copy()
df_copy

Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0            3              1        1        neutral            normal   
1            3              1        1        neutral            normal   
2            3              1        1        neutral            normal   
3            3              1        1        neutral            normal   
4            3              1        2           calm            normal   
...        ...            ...      ...            ...               ...   
2447         3              2        6           fear            normal   
2448         3              2        6           fear            strong   
2449         3              2        6           fear            strong   
2450         3              2        6           fear            strong   
2451         3              2        6           fear            strong   

      Statement  Repetition  Actor  Gender  \
0             1           1      1    male   
1             1           2      1    male   
2             2           1      1    male   
3             2           2      1    male   
4             1           1      1    male   
...         ...         ...    ...     ...   
2447          2           2     24  female   
2448          1           1     24  female   
2449          1           2     24  female   
2450          2           1     24  female   
2451          2           2     24  female   

                                                   Path  Mel Spectrogram  \
0     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.002952   
1     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.003416   
2     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.004721   
3     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.004341   
4     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.001624   
...                                                 ...              ...   
2447  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.037530   
2448  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.118704   
2449  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.126680   
2450  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.122824   
2451  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.208337   

        Chroma       Tempo  
0     0.633091  187.500000  
1     0.629568  106.132075  
2     0.619984   82.720588  
3     0.612607   66.176471  
4     0.608243  112.500000  
...        ...         ...  
2447  0.380013  160.714286  
2448  0.384475   86.538462  
2449  0.379459  193.965517  
2450  0.393004  114.795918  
2451  0.397366  181.451613  

[2452 rows x 13 columns]

In [509]:
#
mel_spec, mfcc, chroma, tempo = extract_features(df_copy['Path'][20])

mfcc

array([-715.8727   ,   74.9853   ,    2.9195237,   11.441712 ,
          6.9607286,   13.466071 ,   -6.72605  ,    4.7315598,
         -6.0603504,   -5.0608444,   -7.6180463,   -3.5482144,
         -1.2796025], dtype=float32)

In [517]:
#
mel_spec, mfcc, chroma, tempo = extract_features(df_copy['Path'][20])

columns = [f"MFCC_{i+1}" for i in range(13)]
dataftest = pd.DataFrame(columns=columns)

for index, row in dataftest.iterrows():
    # Stockez les caractéristiques résumées dans le DataFrame
    if mfcc is not None:
        df_copy.at[index, [f"MFCC_{i+1}" for i in range(13)]] = mfcc

In [518]:
dataftest

Empty DataFrame
Columns: [MFCC_1, MFCC_2, MFCC_3, MFCC_4, MFCC_5, MFCC_6, MFCC_7, MFCC_8, MFCC_9, MFCC_10, MFCC_11, MFCC_12, MFCC_13]
Index: []

In [501]:
for n in range(1,13+1):
    df_copy[f"MFCC_{n}"] = None

df_copy.head()

Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0         3              1        1        neutral            normal   
1         3              1        1        neutral            normal   
2         3              1        1        neutral            normal   
3         3              1        1        neutral            normal   
4         3              1        2           calm            normal   

   Statement  Repetition  Actor Gender  \
0          1           1      1   male   
1          1           2      1   male   
2          2           1      1   male   
3          2           2      1   male   
4          1           1      1   male   

                                                Path  ...  MFCC_4  MFCC_5  \
0  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
1  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
2  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
3  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   
4  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...    None    None   

   MFCC_6 MFCC_7 MFCC_8 MFCC_9 MFCC_10 MFCC_11 MFCC_12 MFCC_13  
0    None   None   None   None    None    None    None    None  
1    None   None   None   None    None    None    None    None  
2    None   None   None   None    None    None    None    None  
3    None   None   None   None    None    None    None    None  
4    None   None   None   None    None    None    None    None  

[5 rows x 26 columns]

In [520]:
columns = [f"MFCC_{i+1}" for i in range(13)]
data = pd.DataFrame(columns=columns)

for index, row in df_copy.iterrows():
    file_path = row['Path']
    mel_spec, mfcc, chroma, tempo = extract_features(file_path)
    # Stockez les caractéristiques résumées dans le DataFrame
    if mfcc is not None:
        df_copy.loc[index, [f"MFCC_{i+1}" for i in range(13)]] = mfcc
#    df_copy.loc[index, 'Mel Spectrogram'] = mel_spec.mean()
#     df.at[index, 'Chroma'] = chroma.mean()            
#     df.at[index, 'Tempo'] = tempo
#     df8 = pd.DataFrame([mfcc], columns=columns)
#     print(df8)
#     data = pd.concat([data, df8], axis=0)
# df = pd.concat([df, data], axis=1)

In [527]:
df_copy.head()
print(df_copy['Mel Spectrogram'])

0       0.002952
1       0.003416
2       0.004721
3       0.004341
4       0.001624
          ...   
2447    0.037530
2448    0.118704
2449    0.126680
2450    0.122824
2451    0.208337
Name: Mel Spectrogram, Length: 2452, dtype: float64


In [523]:
df

Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0            3              1        1        neutral            normal   
1            3              1        1        neutral            normal   
2            3              1        1        neutral            normal   
3            3              1        1        neutral            normal   
4            3              1        2           calm            normal   
...        ...            ...      ...            ...               ...   
2447         3              2        6           fear            normal   
2448         3              2        6           fear            strong   
2449         3              2        6           fear            strong   
2450         3              2        6           fear            strong   
2451         3              2        6           fear            strong   

      Statement  Repetition  Actor  Gender  \
0             1           1      1    male   
1             1           2      1    male   
2             2           1      1    male   
3             2           2      1    male   
4             1           1      1    male   
...         ...         ...    ...     ...   
2447          2           2     24  female   
2448          1           1     24  female   
2449          1           2     24  female   
2450          2           1     24  female   
2451          2           2     24  female   

                                                   Path  Mel Spectrogram  \
0     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.002952   
1     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.003416   
2     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.004721   
3     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.004341   
4     C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.001624   
...                                                 ...              ...   
2447  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.037530   
2448  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.118704   
2449  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.126680   
2450  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.122824   
2451  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...         0.208337   

        Chroma       Tempo  
0     0.633091  187.500000  
1     0.629568  106.132075  
2     0.619984   82.720588  
3     0.612607   66.176471  
4     0.608243  112.500000  
...        ...         ...  
2447  0.380013  160.714286  
2448  0.384475   86.538462  
2449  0.379459  193.965517  
2450  0.393004  114.795918  
2451  0.397366  181.451613  

[2452 rows x 13 columns]

In [526]:
last_n_columns = df_copy.iloc[:, -16:]
print(last_n_columns)

      Mel Spectrogram    Chroma       Tempo      MFCC_1     MFCC_2     MFCC_3  \
0            0.002952  0.633091  187.500000 -726.217224  68.541420   3.293398   
1            0.003416  0.629568  106.132075 -719.128296  70.201569   1.168397   
2            0.004721  0.619984   82.720588 -714.995728  69.689346   3.924564   
3            0.004341  0.612607   66.176471 -710.975281  67.564888   5.782241   
4            0.001624  0.608243  112.500000 -759.921753  75.783524   6.023605   
...               ...       ...         ...         ...        ...        ...   
2447         0.037530  0.380013  160.714286 -576.452820  54.380749  -7.735850   
2448         0.118704  0.384475   86.538462 -510.658813  58.819607 -24.300251   
2449         0.126680  0.379459  193.965517 -510.523682  58.066872 -20.944351   
2450         0.122824  0.393004  114.795918 -491.407776  53.550083 -18.458420   
2451         0.208337  0.397366  181.451613 -486.209534  43.125950 -17.961823   

         MFCC_4     MFCC_5 

In [528]:
# Normaliser les caractéristiques
scaler = StandardScaler()
df_copy[['Mel Spectrogram', 'Chroma', 'Tempo']] = scaler.fit_transform(df_copy[['Mel Spectrogram', 'Chroma', 'Tempo']])

In [529]:
print(df_copy.head())

   Modality  Vocal Channel  Emotion Emotion_string Emotion Intensity  \
0         3              1        1        neutral            normal   
1         3              1        1        neutral            normal   
2         3              1        1        neutral            normal   
3         3              1        1        neutral            normal   
4         3              1        2           calm            normal   

   Statement  Repetition  Actor Gender  \
0          1           1      1   male   
1          1           2      1   male   
2          2           1      1   male   
3          2           2      1   male   
4          1           1      1   male   

                                                Path  ...     MFCC_4  \
0  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...  12.205300   
1  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...  13.122543   
2  C:\Users\doria\OneDrive\Bureau\ECE\ING5\DL\pro...  ...  11.924190   
3  C:\Users\doria\OneDrive

In [530]:
# Convertir les étiquettes d'émotion en encodage one-hot
le = LabelEncoder()
df_copy['Emotion'] = le.fit_transform(df_copy['Emotion'])
y = to_categorical(df_copy['Emotion'], len(EMOTIONS))

# Séparer les données en ensembles d'entraînement et de test
X_train, X_test, y_train, y_test = train_test_split(df_copy.iloc[:, -16:], y, test_size=0.2, random_state=42)

In [532]:
print(X_train.shape, X_test.shape, y_train.shape, y_test.shape)
print(y_train)
print("------")
print(y_test)

(1961, 16) (491, 16) (1961, 8) (491, 8)
[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 1. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 1. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
------
[[0. 0. 1. ... 0. 0. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 1. 0. ... 0. 0. 0.]
 [0. 0. 1. ... 0. 0. 0.]]


In [554]:
# Définir le modèle
model = Sequential()
early_stopping = EarlyStopping(patience=15, restore_best_weights=True)
model_checkpoint = ModelCheckpoint('best_model_weights.h5', save_best_only=True)

#add cnn model
model.add(Conv1D(32, 5, padding='same', input_shape=(X_train.shape[1],1)))
model.add(MaxPooling1D(pool_size=2, padding='same'))
model.add(BatchNormalization())
model.add(Conv1D(16, 5, padding='same'))
model.add(MaxPooling1D(pool_size=2, padding='same'))
model.add(BatchNormalization())
model.add(Dropout(0.25))

model.add(Conv1D(64, 3, padding='same'))
model.add(MaxPooling1D(pool_size=2, padding='same'))
model.add(Conv1D(64, 3, padding='same'))
model.add(BatchNormalization())
model.add(Dropout(0.25))

# Ajouter une couche LSTM
model.add(LSTM(64, return_sequences=True))
model.add(LSTM(32, return_sequences=True))

model.add(Flatten())
model.add(Dense(256, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(len(EMOTIONS), activation='softmax'))

# Compiler le modèle
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Entraîner le modèle
model.fit(X_train, y_train, epochs=90, batch_size=64, validation_split=0.2, verbose=1, callbacks=[early_stopping, model_checkpoint])

# Prédire sur l'ensemble de test
y_pred = model.predict(X_test)
y_pred_labels = np.argmax(y_pred, axis=1)
y_test_labels = np.argmax(y_test, axis=1)

Epoch 1/90
25/25 [==============================] - 12s 97ms/step - loss: 2.0250 - accuracy: 0.2149 - val_loss: 2.1762 - val_accuracy: 0.1221
Epoch 2/90
25/25 [==============================] - 1s 23ms/step - loss: 1.8617 - accuracy: 0.2628 - val_loss: 2.4577 - val_accuracy: 0.1221
Epoch 3/90
25/25 [==============================] - 1s 22ms/step - loss: 1.8339 - accuracy: 0.2691 - val_loss: 2.5145 - val_accuracy: 0.1221
Epoch 4/90
25/25 [==============================] - 1s 22ms/step - loss: 1.8227 - accuracy: 0.2755 - val_loss: 2.6055 - val_accuracy: 0.1221
Epoch 5/90
25/25 [==============================] - 1s 22ms/step - loss: 1.8167 - accuracy: 0.2819 - val_loss: 2.2854 - val_accuracy: 0.1349
Epoch 6/90
25/25 [==============================] - 1s 25ms/step - loss: 1.8009 - accuracy: 0.2838 - val_loss: 2.1617 - val_accuracy: 0.1679
Epoch 7/90
25/25 [==============================] - 1s 26ms/step - loss: 1.7889 - accuracy: 0.2902 - val_loss: 1.8519 - val_accuracy: 0.2468
Epoch 8/90
2

In [555]:
print(model.summary())

Model: "sequential_111"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv1d_302 (Conv1D)         (None, 16, 32)            192       
                                                                 
 max_pooling1d_91 (MaxPooli  (None, 8, 32)             0         
 ng1D)                                                           
                                                                 
 batch_normalization_14 (Ba  (None, 8, 32)             128       
 tchNormalization)                                               
                                                                 
 conv1d_303 (Conv1D)         (None, 8, 16)             2576      
                                                                 
 max_pooling1d_92 (MaxPooli  (None, 4, 16)             0         
 ng1D)                                                           
                                                    

In [280]:

# Définir le modèle
model = Sequential()

# Ajouter les couches entièrement connectées
model.add(Dense(128, activation='relu'))
model.add(Dropout(0.5))
model.add(Dense(64, activation='relu'))
model.add(Dense(len(EMOTIONS), activation='softmax'))

# Compiler le modèle
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Entraîner le modèle
model.fit(X_train, y_train, epochs=15, batch_size=32, validation_split=0.2, verbose=1)

# Prédire sur l'ensemble de test
y_pred = model.predict(X_test)
y_pred_labels = np.argmax(y_pred, axis=1)
y_test_labels = np.argmax(y_test, axis=1)

# Évaluer les performances
accuracy = accuracy_score(y_test_labels, y_pred_labels)
conf_mat = confusion_matrix(y_test_labels, y_pred_labels)
class_report = classification_report(y_test_labels, y_pred_labels)

print(f'Accuracy: {accuracy}')
print(f'Confusion Matrix:\n{conf_mat}')
print(f'Classification Report:\n{class_report}')

Epoch 1/15
49/49 [==============================] - 2s 11ms/step - loss: 2.0215 - accuracy: 0.1913 - val_loss: 1.9456 - val_accuracy: 0.2087
Epoch 2/15
49/49 [==============================] - 0s 4ms/step - loss: 1.9357 - accuracy: 0.2449 - val_loss: 1.9132 - val_accuracy: 0.2061
Epoch 3/15
49/49 [==============================] - 0s 5ms/step - loss: 1.8953 - accuracy: 0.2583 - val_loss: 1.8946 - val_accuracy: 0.2239
Epoch 4/15
49/49 [==============================] - 0s 4ms/step - loss: 1.8625 - accuracy: 0.2730 - val_loss: 1.8835 - val_accuracy: 0.2417
Epoch 5/15
49/49 [==============================] - 0s 5ms/step - loss: 1.8475 - accuracy: 0.2755 - val_loss: 1.8579 - val_accuracy: 0.2570
Epoch 6/15
49/49 [==============================] - 0s 4ms/step - loss: 1.8293 - accuracy: 0.2844 - val_loss: 1.8573 - val_accuracy: 0.2468
Epoch 7/15
49/49 [==============================] - 0s 4ms/step - loss: 1.8265 - accuracy: 0.2902 - val_loss: 1.8563 - val_accuracy: 0.2824
Epoch 8/15
49/49 [=

In [15]:
mel_spectrograms = []
signals = []
for i, file_path in enumerate(df['Path']):
    audio, sample_rate = lr.load(file_path, duration=3, offset=0.5, sr=sr)
    signal = np.zeros((int(sr*3,)))
    signal[:len(audio)] = audio
    signals.append(signal)
    print("\r Processed {}/{} files".format(i, len(df)), end='')
signals = np.stack(signals, axis=0)

 Processed 1959/1960 files

La liste signals stocke les signaux audio extraits de chaque fichier. Chaque élément de la liste est un tableau NumPy représentant un signal audio de 3 secondes, ou de la durée spécifiée. Ces signaux seront utilisés comme données d'entrée pour la suite du prétraitement.

Une boucle itère sur chaque chemin de fichier dans la colonne 'Path' du DataFrame df.

Utilisation de la fonction load de Librosa pour charger le fichier audio à partir du chemin spécifié (file_path). Les paramètres duration=3 et offset=0.5 spécifient la durée du fichier audio à charger (3 secondes) et le décalage (offset) à partir du début du fichier (0.5 seconde). 

signal = np.zeros((int(SAMPLE_RATE * 3,))) : Création d'un tableau NumPy de taille correspondant à 3 secondes de signal audio (ou la durée spécifiée) avec un échantillonnage constant. On initialise ce tableau avec des zéros.

signal[:len(audio)] = audio : Remplissage de la partie du tableau avec le signal audio réel chargé. Cela permet d'ajuster la longueur du signal si elle est inférieure à 3 secondes.

signals = np.stack(signals, axis=0) : Conversion de la liste signals en un tableau NumPy bidimensionnel où chaque ligne représente un signal audio. Le résultat est stocké dans la variable signals qui sera utilisée ultérieurement dans le script.
